# Setup

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from accelerate import Accelerator, load_checkpoint_and_dispatch
import os

# setup the model
model = MODELS[CONFIG["model_type"]]

accelerator = Accelerator()

#model = accelerator.prepare(model)

PATH = CONFIG["PATH"]
MODELNAME = CONFIG["modelname"]

# optionally: load the model
save_directory = f"{PATH}/model/{MODELNAME}"
file_path = f"{save_directory}/model.safetensors"

if os.path.exists(file_path):
    model = load_checkpoint_and_dispatch(model, file_path)
    print("Loaded!")
else:
    print("Failed to load")

MODELNAME

/Users/midataur/Documents/Python/sts-analysis/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


ModuleNotFoundError: No module named 'core'

In [13]:
from core.utilities import *
from core.state_analysis import extract_states_and_choices

path = f"./run_data/train"

runs = extract_runs(path, verbose=True)
states, choices = extract_states_and_choices(runs, verbose=True)

Extracting states and choices: 100%|██████████| 13006/13006 [00:03<00:00, 3423.61it/s]


In [6]:
from utilities import *
from state_analysis import extract_states

path = f"../run_data/train"

runs = extract_runs(path, verbose=True)
states = extract_states(runs, verbose=True, strict=True)

Extracting states: 100%|██████████| 13006/13006 [00:04<00:00, 2786.18it/s]


# Model investigation

In [7]:
index = 1

small_states = [states[index]]
small_choices = [choices[index]]

probs = model.gen_from_states(small_states, small_choices, CONFIG)[0]

TypeError: V2.gen_from_states() missing 1 required positional argument: 'config'

In [165]:
states[index]

{'ascension': 13,
 'character': 'IRONCLAD',
 'current_hp': 56,
 'deck': ['AscendersBane',
  'Defend_R',
  'Defend_R',
  'Defend_R',
  'Defend_R+1',
  'Shockwave+1',
  'Inflame+1',
  'Bash',
  'Strike_R',
  'Strike_R',
  'Strike_R'],
 'floor': 1,
 'gold': 373,
 'max_hp': 80,
 'relics': [],
 'victory': True}

In [166]:
choices[index]

{'options': ['True Grit', 'Bloodletting', 'Battle Trance'],
 'picked': 'Battle Trance'}

In [167]:
output_set = AUGMENTED_CARDS_LIST

labelled = list(zip(output_set, probs))
labelled.sort(key=lambda x: x[1], reverse=True)

for thing, prob in labelled[:10]:
    print(thing, "%.4f"%prob.item())

Nirvana 1.0000
Noxious Fumes 0.0000
Crippling Poison 0.0000
Meteor Strike+1 0.0000
Enlightenment 0.0000
Prepared 0.0000
Gash 0.0000
Catalyst 0.0000
Burning Pact 0.0000
EMPTY 0.0000


In [168]:
for thing, prob in labelled:
    if thing == "SKIP":
        print(prob.item())

0.0


In [169]:
mat = model.cont_embedding_transformation.weight.detach().numpy().transpose()
px.imshow(mat.dot(mat.transpose()))

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'coloraxis': 'coloraxis',
              'hovertemplate': 'x: %{x}<br>y: %{y}<br>color: %{z}<extra></extra>',
              'name': '0',
              'type': 'heatmap',
              'xaxis': 'x',
              'yaxis': 'y',
              'z': {'bdata': ('MWC2QVa9qr8osxw/jCyCP7g8Aj9t+c' ... 'nCvyJI8b7uuf89SFrRPgivxL0G8qZB'),
                    'dtype': 'f4',
                    'shape': '6, 6'}}],
    'layout': {'coloraxis': {'colorscale': [[0.0, '#0d0887'], [0.1111111111111111,
                                            '#46039f'], [0.2222222222222222,
                                            '#7201a8'], [0.3333333333333333,
                                            '#9c179e'], [0.4444444444444444,
                                            '#bd3786'], [0.5555555555555556,
                                            '#d8576b'], [0.6666666666666666,
                                            '#ed7953'], [0.7777777777777778,
                                            '#fb9f3a'], [0.8888888888888888,
                                            '#fdca26'], [1.0, '#f0f921']]},
               'margin': {'t': 60},
               'template': '...',
               'xaxis': {'anchor': 'y', 'constrain': 'domain', 'domain': [0.0, 1.0], 'scaleanchor': 'y'},
               'yaxis': {'anchor': 'x', 'autorange': 'reversed', 'constrain': 'domain', 'domain': [0.0, 1.0]}}
})

In [170]:
"ascension", 0
"current_hp", 1
"floor", 2
"gold", 3
"max_hp", 4
"victory", 5

('victory', 5)

# Embedding pictures

In [171]:
import plotly.express as px
import numpy as np
import torch

# embedding = model.choice_token_embedding_table(
#     torch.arange(len(AUGMENTED_CARDS_LIST))
# ).detach().numpy()

embedding = model.state_token_embedding_table(
    torch.arange(len(VOCABULARY))
).detach().numpy()

similarity = []

for x in embedding:
    row = []
    for y in embedding:
        row.append(np.dot(x, y)/(np.linalg.norm(x)*np.linalg.norm(y)))
    similarity.append(row)

similarity = np.array(similarity)

figure = px.imshow(
    similarity,
    title=f"{MODELNAME} state embedding similarity matrix"
)

hide_ui = True

if hide_ui:
    figure.update_layout(coloraxis_showscale=True)
    figure.update_xaxes(showticklabels=False)
    figure.update_yaxes(showticklabels=False)
    figure.update_layout(
        title="",
        autosize=False,
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0,
            pad=0
        )
    )

figure

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'coloraxis': 'coloraxis',
              'hovertemplate': 'x: %{x}<br>y: %{y}<br>color: %{z}<extra></extra>',
              'name': '0',
              'type': 'heatmap',
              'xaxis': 'x',
              'yaxis': 'y',
              'z': {'bdata': ('AQCAP2FG8DsfWIM8Nk0qvSqIz7yYSm' ... '0auwqPNr3FtIi9tiKUPF/h3jwAAIA/'),
                    'dtype': 'f4',
                    'shape': '891, 891'}}],
    'layout': {'autosize': False,
               'coloraxis': {'colorscale': [[0.0, '#0d0887'], [0.1111111111111111,
                                            '#46039f'], [0.2222222222222222,
                                            '#7201a8'], [0.3333333333333333,
                                            '#9c179e'], [0.4444444444444444,
                                            '#bd3786'], [0.5555555555555556,
                                            '#d8576b'], [0.6666666666666666,
                                            '#ed7953'], [0.7777777777777778,
                                            '#fb9f3a'], [0.8888888888888888,
                                            '#fdca26'], [1.0, '#f0f921']],
                             'showscale': True},
               'margin': {'b': 0, 'l': 0, 'pad': 0, 'r': 0, 't': 0},
               'template': '...',
               'title': {'text': ''},
               'xaxis': {'anchor': 'y',
                         'constrain': 'domain',
                         'domain': [0.0, 1.0],
                         'scaleanchor': 'y',
                         'showticklabels': False},
               'yaxis': {'anchor': 'x',
                         'autorange': 'reversed',
                         'constrain': 'domain',
                         'domain': [0.0, 1.0],
                         'showticklabels': False}}
})

In [172]:
VOCABULARY[24:46]

['Amplify',
 'Amplify+1',
 'Anger',
 'Anger+1',
 'Apotheosis',
 'Apotheosis+1',
 'Armaments',
 'Armaments+1',
 'AscendersBane',
 'Auto Shields',
 'Auto Shields+1',
 'Backflip',
 'Backflip+1',
 'Backstab',
 'Backstab+1',
 'Ball Lightning',
 'Ball Lightning+1',
 'Bandage Up',
 'Bandage Up+1',
 'Bane',
 'Bane+1',
 'Barrage']

# Give suggestions for current game

In [ ]:
from utilities import get_current_save
from state_analysis import extract_from_save

SAVES_DIRECTORY = "/Users/midataur/Library/Application Support/Steam/steamapps/common/SlayTheSpire/SlayTheSpire.app/Contents/Resources/saves"

save, char = get_current_save(SAVES_DIRECTORY)

state = extract_from_save(save, char)

# adjust to adjust perceived strength
state["victory"] = True
state["ascension"] = 9

# manually add a relic
new_relic = "Boot"
add_relic = False

if add_relic:
    if new_relic not in RELICS_LIST:
        raise Exception(f"Unknown relic {new_relic}. Perhaps a mispelling?")
    elif new_relic in state["relics"]:
        raise Exception(f"Tried to add duplicate relic {new_relic}. Comment this out.")

    state["relics"].append(new_relic)

# need to input choices manually
choice = {
    "options": [
        "Flying Knee+1",
        "Quick Slash+1",
        "Dodge and Roll",
        "SKIP"
    ],
    "picked": "SKIP" # arbitrary
}

for card in choice["options"]:
    if card not in AUGMENTED_CARDS_LIST:
        raise Exception(f"Unknown card {card}. Perhaps a misspelling?")

probs = model.gen_from_states([state], [choice], CONFIG)[0]

output_set = AUGMENTED_CARDS_LIST

labelled = list(zip(output_set, probs))

# extract only the actual choices
real_choices = []

norm_constant = 0

for card, prob in labelled:
    if card in choice["options"]:
        real_choices.append((card, prob))
        norm_constant += prob

real_choices.sort(key=lambda x: x[1], reverse=True)

for thing, prob in real_choices:
    real_prob = prob.item()/norm_constant
    print(thing, "%.4f"%real_prob)

Dodge and Roll nan
Flying Knee+1 nan
Quick Slash+1 nan
SKIP nan


In [151]:
state

{'ascension': 9,
 'character': 'THE_SILENT',
 'current_hp': 54,
 'deck': ['Survivor',
  'Neutralize',
  'Infinite Blades',
  'Masterful Stab',
  'Calculated Gamble+1',
  'Backflip',
  'Prepared',
  'Terror',
  'Noxious Fumes',
  'Glass Knife+1',
  'Blade Dance',
  'Footwork',
  'Well Laid Plans+1',
  'Acrobatics',
  'Outmaneuver',
  'Footwork',
  'Adrenaline',
  'Wraith Form v2',
  'Choke',
  'After Image+1',
  'Acrobatics',
  'Dark Shackles',
  'After Image+1'],
 'floor': 38,
 'gold': 12,
 'max_hp': 65,
 'relics': ['Ring of the Snake',
  'NeowsBlessing',
  'Orichalcum',
  'MealTicket',
  'Ancient Tea Set',
  'Golden Idol',
  "Pandora's Box",
  'Letter Opener',
  'Bronze Scales',
  'Eternal Feather',
  'Frozen Egg 2',
  'Red Mask',
  'Cursed Key',
  'Gremlin Horn'],
 'victory': True}

In [ ]:
save

{'shuffle_seed_count': 0,
 'metric_purchased_purges': 0,
 'metric_path_per_floor': [],
 'monster_list': ['Small Slimes',
  'Cultist',
  'Jaw Worm',
  'Blue Slaver',
  'Looter',
  'Large Slime',
  'Exordium Wildlife',
  '3 Louse',
  'Blue Slaver',
  'Large Slime',
  'Exordium Thugs',
  '3 Louse',
  'Blue Slaver',
  '2 Fungi Beasts',
  'Exordium Thugs',
  'Gremlin Gang'],
 'metric_potions_floor_spawned': [],
 'daily_mods': [],
 'metric_campfire_choices': [],
 'is_ascension_mode': True,
 'metric_items_purchased': [],
 'is_endless_mode': False,
 'merchant_seed_count': 0,
 'floor_num': 0,
 'uncommon_relics': ['HornCleat',
  'Meat on the Bone',
  'Frozen Egg 2',
  'StrikeDummy',
  'Shuriken',
  'Self Forming Clay',
  'Bottled Flame',
  'White Beast Statue',
  'Paper Frog',
  'Singing Bowl',
  'Blue Candle',
  'Mummified Hand',
  'The Courier',
  'Pear',
  'Bottled Lightning',
  'Kunai',
  'Letter Opener',
  'Darkstone Periapt',
  'Bottled Tornado',
  'Pantograph',
  'Ornamental Fan',
  'InkB

# Genuine scratchpad

In [ ]:
states[4]

{'ascension': 1,
 'character': 'DEFECT',
 'current_hp': 57,
 'deck': ['Strike_B+1',
  'Defend_B',
  'Defend_B',
  'Defend_B+1',
  'Dualcast+1',
  'Cold Snap+1',
  'Auto Shields+1',
  'Tempest+1',
  'Gash+1',
  'Parasite',
  'Redo',
  'Zap',
  'Defend_B'],
 'deck_size': 13,
 'floor': 4,
 'floors_to_boss': 12,
 'gold': 150,
 'max_hp': 75,
 'n_attacks': 3,
 'n_curses': 0,
 'n_powers': 0,
 'n_relics': 0,
 'n_skills': 4,
 'relics': [],
 'victory': True}

In [35]:
import torch

len(torch.ones((1,2,3)).shape)

3

In [ ]:
torch.rand(64).round()

tensor([0., 1., 0., 0., 0., 1., 1., 1., 1., 0., 1., 0., 0., 1., 0., 0., 1., 0.,
        0., 0., 0., 1., 1., 0., 0., 0., 0., 1., 1., 0., 0., 0., 1., 0., 1., 1.,
        1., 0., 1., 0., 1., 1., 0., 0., 1., 1., 0., 0., 1., 0., 1., 0., 0., 0.,
        1., 0., 1., 0., 1., 0., 0., 0., 0., 0.])

In [10]:
from dataloading import get_dataset_and_loader
from main import CONFIG

CONFIG["PATH"] = ".."

ds, dl = get_dataset_and_loader("train", CONFIG)

In [11]:
ds.targets.mean()

tensor(0.2227)

In [ ]:
runs[0]["gold_per_floor"]

[109, 120, 195, 205, 205, 205, 205]

In [40]:
runs[0]["floor_reached"]

6

In [9]:
states[2]

{'ascension': 1,
 'character': 'DEFECT',
 'current_hp': 57,
 'deck': ['Strike_B+1',
  'Defend_B',
  'Defend_B',
  'Defend_B+1',
  'Dualcast+1',
  'Cold Snap+1',
  'Auto Shields+1',
  'Tempest+1',
  'Parasite',
  'Redo',
  'Zap',
  'Defend_B'],
 'deck_size': 12,
 'floor': 2,
 'floors_to_boss': 14,
 'gold': 184,
 'max_hp': 75,
 'n_attacks': 2,
 'n_curses': 0,
 'n_powers': 0,
 'n_relics': 0,
 'n_skills': 4,
 'relics': [],
 'victory': True}

In [22]:
import torch

t = torch.empty((0,200))

a = torch.ones((19064, 200))

torch.cat((t,a))

tensor([[1., 1., 1.,  ..., 1., 1., 1.],
        [1., 1., 1.,  ..., 1., 1., 1.],
        [1., 1., 1.,  ..., 1., 1., 1.],
        ...,
        [1., 1., 1.,  ..., 1., 1., 1.],
        [1., 1., 1.,  ..., 1., 1., 1.],
        [1., 1., 1.,  ..., 1., 1., 1.]])

In [26]:
from utilities import tokenize

a = [1,2,3]

a.index("a")

ValueError: 'a' is not in list

In [49]:
from multiprocessing import Queue, Pool

def interate_queue(queue):
    while not queue.empty():
        yield queue.get()

def square(x):
    return x**2

queue = Queue()

with Pool() as p:
    for x in p.imap_unordered(square, range(20)):
        queue.put(x)

print(queue.empty())

# empty queue
for x in interate_queue(queue):
    print(x)

Process SpawnPoolWorker-29:
Process SpawnPoolWorker-31:
Traceback (most recent call last):
Traceback (most recent call last):
Process SpawnPoolWorker-32:
Process SpawnPoolWorker-30:
Traceback (most recent call last):
Traceback (most recent call last):
Process SpawnPoolWorker-33:
  File "/opt/homebrew/Cellar/python@3.13/3.13.2/Frameworks/Python.framework/Versions/3.13/lib/python3.13/multiprocessing/process.py", line 313, in _bootstrap
    self.run()
    ~~~~~~~~^^
  File "/opt/homebrew/Cellar/python@3.13/3.13.2/Frameworks/Python.framework/Versions/3.13/lib/python3.13/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
    ~~~~~~~~~~~~^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/homebrew/Cellar/python@3.13/3.13.2/Frameworks/Python.framework/Versions/3.13/lib/python3.13/multiprocessing/pool.py", line 114, in worker
    task = get()
  File "/opt/homebrew/Cellar/python@3.13/3.13.2/Frameworks/Python.framework/Versions/3.13/lib/python3.13/multiprocessing/

KeyboardInterrupt: 

In [51]:
import torch
import weakref

a = torch.tensor([1,2,3])

a._fix_weakref()

In [3]:
import torch

a = torch.ones((7,1)).reshape(-1)